In [1]:
%reload_ext autoreload
%autoreload 2
from simulation_v3 import Sim
from simulation_v3 import SimTester

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from matplotlib import style
import pandas as pd
import os
import sys
import time


In [29]:
# In matrix form using the new method:

# define the network adjacency matrix
    # Servers/Sources/Queues defined on diagional as:
    # 1 on diagonal: customer arrives
    # -1 on diagonal: server with service time
    # 0 on diagonal: server with no service time
        # customer can only move to a server if not busy

    # Connections between elements of system defined off diagonal as:
    # sum(non-diagonal) = 1:
        # entries are the probability of a customer moving from one element to another
    # sum(non-diagonal) > 1 (ie, each child node has 1 in adj matrix):
        # send customers to all child node with shortest queue
    # sum(non-diagonal) = 0:
        # server leads to a sink

adj_sim    = np.array([ [ 1,  0.5,   0,   0,     0.25,  0.25,   0,    0 ],
                        [ 0, -0.9,  0.6,  0,     0.15,  0.25,   0,    0 ],
                        [ 0,  0,   -0.5,  0,     0,     0,      0,    0 ],
                        [ 0,  0,    0.5,  1,     0,     0.5,    0,    0 ],
                        [ 0,  0,    0,    0,     -0.942, 0,      0.7,  0.3 ], 
                        [ 0,  0.1,  0.3,  0,     0.5,  -0.7432,   0.1,  0 ], 
                        [ 0,  0,    0,    0,     0,     0,    -0.8432,   0 ],
                        [ 0,  0,    0.1,  0,     0.6,   0.1,   0.2,  -0.9543 ],])

# max queue lengths ( not too important with so few customers and long server time for each event)
# can be changed later when mixing more notes and using a larger matrix. 
queue_list = [127,127,127,127,127,127,127,127]

# define the distributions for each server
    # name of distribution, parameters (example: ['exponential', mean=1.0])
distributions = [['normal', 8, 3],
                 ['normal', 0.75, 0.5],
                 ['normal', 0.64, 0.1],
                 ['normal', 0.5, 0.2],
                 ['normal', 5, 3],
                 ['normal', 0.723, 0.1],
                 ['normal', 0.41, 5],
                 ['normal', 0.67, 2],
                 ['normal', 0.67, 2]]

np.random.seed(42)
seeds = np.random.randint(0, 99999, size=1)
sim = Sim(adj_sim, distributions, queue_list, seeds=seeds, generate_log=True, animation=False, record_history=False, logging_mode='Music')

sim.run(number_of_customers=1000)

1: 0.44902801513671875 elapsed time for 466.08178264784436 simulation time with 1000 customers


In [9]:
%reload_ext autoreload
%autoreload 2

from sim_log_process_music import process_adjsim_log

# this file is still very rough.... The note levels are being randomly selected 30-127

# velcoity are based off queue length

# Only using mod 2 as a way to create "quiet" time. Might need this to be a parameter the network outputs such that certain events can be "quiet" and others can be "loud"

# many more tuning improvements to be made - Change the matrix above for highly variable output. 

process_adjsim_log()

In [110]:
# generate a random nxn matrix where the sum of each row except the diagonal is 1
# this will be the adj matrix
# generate a random distribution for each server
size = 32
sources = size // 8
matrix = np.random.rand(size,size)

# randomly select source and sink nodes
sources = np.random.choice(size, sources, replace=False)

# set the values of all columns to 0 for columns that are sources or sinks
for i in sources:
    matrix[:,i] = 0
    matrix[i,i] = 0

for i in [x for x in np.arange(0,size) if x not in sources]:
    matrix[i][i] = 0

# normalize the matrix where the sum of each row is 1 except for the diagonal
for i in range(size):
    matrix[i] = matrix[i] / sum(matrix[i])

# set the values of diagonals according to source and sink nodes
for i in sources:
    matrix[i,i] = 1.0

for i in [x for x in np.arange(0,size) if x not in sources]:
    matrix[i][i] = -1.0

# create a random distribution for each server
distributions = []
for i in range(size):
    distributions.append(['normal', np.random.rand(), np.random.rand()])

# create a random queue list
queue_list = np.random.randint(50, 126, size=size)

# randomly choose the instruments for each server
instruments = np.random.randint(0, 45, size=size)

# check that the matrix is valid by trying to create a simulation and checking for errors
try:
    np.random.seed(42)
    seeds = np.random.randint(0, 99999, size=1)
    sim = Sim(matrix, distributions, queue_list, seeds=seeds, generate_log=True, animation=False, record_history=False, logging_mode='Music')
    sim.run(number_of_customers=100)
except Exception as e:
    print(e)
    print(e.args)
    print('Invalid matrix')

filepath = process_adjsim_log(instruments=instruments)


1: 0.10399961471557617 elapsed time for 9.644402976762656 simulation time with 100 customers


In [2]:
from midi2audio import FluidSynth
import os

file_path = r'S:\Sadie\2024\475\Project\song-extender\experimenting with adjsims\adj_sim_outputs\midi\output.mid'
print(os.path.exists(file_path))

# using the default sound font in 44100 Hz sample rate
fs = FluidSynth(sound_font='FluidR3_GM.sf2')
fs.midi_to_audio('output.mid', 'output.wav')


True


In [36]:
import IPython.display as ipd
ipd.Audio('output.wav')


In [64]:
import librosa
import time

%reload_ext autoreload
%autoreload 2

from sim_log_process_music import process_adjsim_log

def get_melspectrogram_db(file_path, sr=44100, n_fft=2048, hop_length=512, n_mels=128, fmin=20, fmax=8300, top_db=80):
    y, sr = librosa.load(file_path, sr=sr, mono=True)
    mel = librosa.feature.melspectrogram(y=y, sr=sr, n_fft=n_fft, hop_length=hop_length, n_mels=n_mels, fmin=fmin, fmax=fmax)
    mel = librosa.power_to_db(mel, ref=np.max)
    return mel

def matrix_to_wav(matrices=[None]*5, size=32, use_same_instrument=None):
    num_aug = 5
    spectrograms = np.zeros((len(matrices), 128, 216))
    for index, matrix in enumerate(matrices):
        if matrix != None:
            matrix = np.random.rand(size,size)
            # zero out ends of each row
            matrix[size-num_aug:,:] = 0
            matrix[:,size-num_aug:] = 0
            
            # for the last 4 rows up to the 24th column, randomly set the values between 0 and 1
            matrix[size-num_aug, :size-num_aug] = np.random.rand(size-num_aug)
            matrix[size-num_aug+1, :size-num_aug] = np.random.rand(size-num_aug)
            matrix[size-num_aug+2, :size-num_aug] = np.random.rand(size-num_aug)
            matrix[size-num_aug+3, :size-num_aug] = np.random.rand(size-num_aug)
            matrix[size-num_aug+4, :size-num_aug] = np.random.rand(size-num_aug)

        # select source and sink nodes based on the values in the 23rd row where the values are between 0 and 1
        sources = np.where(matrix[size-num_aug] > 0.75)
        if len(sources) == 0:
            sources = np.random.choice(size-num_aug, size=size//8, replace=False)


        instruments = np.zeros(size-num_aug)
        # select instruments for each server based on the values in 24th row where the values are between 0 and 1 and the instrument is selected based on the value up to 128
        if use_same_instrument == None:
            for i in range(size-num_aug):
                instruments[i] = int(matrix[size-num_aug+1,i] * 127)
        else:
            instruments = np.array([use_same_instrument]*(size-num_aug))
        #print("Instruments:", instruments)


        # create a note level for each server based on the values in the 27th row where the values are between 0 and 1 and the note level is selected based on the value up to 127
        note_levels = np.zeros(size-num_aug)
        for i in range(size-num_aug):
            note_levels[i] = int(matrix[size-num_aug+2,i] * 127) 
        #print("Note levels:", note_levels)
        #print("len(note_levels):", len(note_levels))

        # create a normal distribution for each server based on the values in the 25th and 26th rows where the values are between 0 and 1
        distributions = []
        for i in range(size-num_aug):
            #distributions.append(['exponential', 1+matrix[size-num_aug+2,i]])
            if i in sources[0]:
                distributions.append(['normal', 10*matrix[size-num_aug+3,i], 5*matrix[size-num_aug+4,i]])
            else:
                distributions.append(['normal', 3*matrix[size-num_aug+3,i], 2*matrix[size-num_aug+4,i]])
        #print("Distributions:", distributions)

        for i in sources:
            matrix[:,i] = 0
            matrix[i,i] = 0

        for i in [x for x in np.arange(0,size) if x not in sources[0]]:
            matrix[i][i] = 0

        for i in range(size-num_aug):
            matrix[i] = matrix[i] / sum(matrix[i])

        for i in sources:
            matrix[i,i] = 1.0

        for i in [x for x in np.arange(0,size-num_aug) if x not in sources[0]]:
            matrix[i][i] = -1.0

        queue_list = [127] * size
        length_mel = 0
        while length_mel < 216:
            np.random.seed(np.random.randint(0, 99999, size=1))
            seeds = np.random.randint(0, 99999, size=1)
            sim_matrix = matrix[:size-num_aug, :size-num_aug]
            sim = Sim(sim_matrix, distributions, queue_list, seeds=seeds, generate_log=True, animation=False, record_history=False, logging_mode='Music')
            sim.run(number_of_customers=1000)

            file_path = process_adjsim_log(instruments=instruments, note_levels=note_levels)

            fs = FluidSynth(sound_font='FluidR3_GM.sf2', sample_rate=44100)

            output_file = 'adj_sim_outputs\wav\output_'+ str(index) + '.wav'

            # check if the file path exists, if not, create the file
            if not os.path.exists(output_file):
                print('Creating wav file:', output_file)
                os.makedirs(os.path.dirname(output_file), exist_ok=True)
                with open(output_file, 'w') as f:
                    f.write('')

            fs.midi_to_audio(file_path, output_file)

            print('Generated wav file:', output_file)

            time.sleep(0.2)
            # create a mel spectrogram for the wav file and save it
            mel = get_melspectrogram_db(file_path=output_file)
            length_mel = mel.shape[1]

        spectrograms[index] = mel[:128, :216]

    # return numpy array for first 5 seconds of each spectrogram
    return spectrograms

_ = matrix_to_wav(use_same_instrument=0)
#_ = matrix_to_wav()

1: 0.17599940299987793 elapsed time for 5.091043535670813 simulation time with 1000 customers
Generated wav file: adj_sim_outputs\wav\output_0.wav
1: 0.21703147888183594 elapsed time for 14.341102596902285 simulation time with 1000 customers
Generated wav file: adj_sim_outputs\wav\output_1.wav
1: 0.3040013313293457 elapsed time for 40.25699493073339 simulation time with 1000 customers
Generated wav file: adj_sim_outputs\wav\output_2.wav
1: 0.41699862480163574 elapsed time for 60.02300131106445 simulation time with 1000 customers
Generated wav file: adj_sim_outputs\wav\output_3.wav
1: 0.8919973373413086 elapsed time for 34.03619970980078 simulation time with 1000 customers
Generated wav file: adj_sim_outputs\wav\output_4.wav


In [68]:
instruments = np.array([8]*(8))
instruments

array([8, 8, 8, 8, 8, 8, 8, 8])

In [19]:
# nxn where every elment is 1
matrix = np.ones((8,8))
print(matrix)



[[1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1. 1. 1.]]


In [22]:
matrix[5:,:] = 0
matrix[:,5:] = 0
print(matrix)

[[1. 1. 1. 1. 1. 0. 0. 0.]
 [1. 1. 1. 1. 1. 0. 0. 0.]
 [1. 1. 1. 1. 1. 0. 0. 0.]
 [1. 1. 1. 1. 1. 0. 0. 0.]
 [1. 1. 1. 1. 1. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0.]]


In [29]:
print(matrix[:5,:5])

[[1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1.]]
